In [46]:
import json

# Opening JSON file
f = open('annual_report_23.json', encoding="utf-8")
 
# returns JSON object as
# a dictionary
data = json.load(f)
 
# Iterating through the json
# list
countEn = 0
countText = 0
training_set = []
for p in data:
    if (p["language"] == "en"):
        countEn = countEn + 1
        for pp in p["text"]:
            #print(pp["text"])
            countText = countText + 1
            #print(pp["ner"])
            ner_str = json.loads(pp["ner"])
            entities_list = []
            for ner in ner_str:
                #ner = json.loads(ner_str)
                #print(ner)
                if len(ner):
                    #print(ner["text"])
                    entities_list.append(tuple((ner["start"],ner["end"],ner["label"])))
            #print(entities_list)
            #if (len(entities_list)):
            training_set.append(tuple((pp["text"],{"entities":entities_list})))
print(countEn)
print(countText)
print(len(training_set))
# Closing file
f.close()

23
3417
3417


In [47]:
# Import and load the spacy model
import spacy
nlp=spacy.load("en_core_web_sm") 

# Getting the ner component
ner=nlp.get_pipe('ner')

for _, annotations in training_set:
  for ent in annotations.get("entities"):
    ner.add_label(ent[2])

# Disable pipeline components you dont need to change
pipe_exceptions = ["ner", "trf_wordpiecer", "trf_tok2vec"]
unaffected_pipes = [pipe for pipe in nlp.pipe_names if pipe not in pipe_exceptions]

In [50]:
# Import requirements
import random
from spacy.util import minibatch, compounding
from pathlib import Path
from spacy.training.example import Example

# TRAINING THE MODEL
with nlp.disable_pipes(*unaffected_pipes):

  # Training for 30 iterations
  for iteration in range(30):

    # shuufling examples  before every iteration
    random.shuffle(training_set)
    losses = {}
    # batch up the examples using spaCy's minibatch
    batches = minibatch(training_set, size=compounding(4.0, 32.0, 1.001))
    for batch in batches:
        for text, annotations in batch:
            # create Example
            doc = nlp.make_doc(text)
            example = Example.from_dict(doc, annotations)
            # Update the model
            nlp.update([example], losses=losses, drop=0.5)
            print("Losses", losses)

Losses {'ner': 4.720925200453266}
Losses {'ner': 8.37194877142603}
Losses {'ner': 9.879912577816793}
Losses {'ner': 22.520690288756573}
Losses {'ner': 45.209763450593485}
Losses {'ner': 45.20977294145264}
Losses {'ner': 46.839761853841466}
Losses {'ner': 56.61592148705343}
Losses {'ner': 60.83634555061062}
Losses {'ner': 64.61395071080926}
Losses {'ner': 64.80745459163927}
Losses {'ner': 64.80747735077375}
Losses {'ner': 68.73145777265518}
Losses {'ner': 68.74184426799955}
Losses {'ner': 69.18096933897041}
Losses {'ner': 71.7356408648615}
Losses {'ner': 74.1293693781693}
Losses {'ner': 92.20814290536657}
Losses {'ner': 96.72514654999163}
Losses {'ner': 113.26778495025926}
Losses {'ner': 123.05625245779109}
Losses {'ner': 126.52541086160868}
Losses {'ner': 145.0448637690496}
Losses {'ner': 150.46746588232094}
Losses {'ner': 154.68162723271533}
Losses {'ner': 154.7078938485438}
Losses {'ner': 165.21326249462032}
Losses {'ner': 166.41826645068193}
Losses {'ner': 179.21439004252045}
Losses

In [66]:
# Testing the model
doc = nlp("I am Mark E Tucker and I work in Investment Risk Management LLC as a Vice President")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])

Entities [('Mark E Tucker', 'PERSON'), ('Investment Risk Management LLC', 'ORG')]


In [53]:
# Save the  model to directory
output_dir = Path('output/')
nlp.to_disk(output_dir)
print("Saved model to", output_dir)

# Load the saved model and predict
print("Loading from", output_dir)
nlp_updated = spacy.load(output_dir)
doc = nlp_updated("Fridge can be ordered in FlipKart" )
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])

Saved model to output
Loading from output
Entities [('FlipKart', 'ORG')]


In [55]:
doc = nlp("Ada Lovelace was born in London")

# Document level
ents = [(e.text, e.label_, e.kb_id_) for e in doc.ents]
print(ents)

[('Ada Lovelace', 'PERSON', ''), ('London', 'GPE', '')]


In [57]:
from spacy.pipeline.entity_linker import DEFAULT_NEL_MODEL
# add pipeline (declared through entry_points in setup.py)
nlp.add_pipe("entityLinker", last=True)

doc = nlp("I watched the Pirates of the Caribbean last silvester")

# returns all entities in the whole document
all_linked_entities = doc._.linkedEntities
# iterates over sentences and prints linked entities
for sent in doc.sents:
    sent._.linkedEntities.pretty_print()

ValueError: [E002] Can't find factory for 'entityLinker' for language English (en). This usually happens when spaCy calls `nlp.create_pipe` with a custom component name that's not registered on the current language class. If you're using a Transformer, make sure to install 'spacy-transformers'. If you're using a custom component, make sure you've added the decorator `@Language.component` (for function components) or `@Language.factory` (for class components).

Available factories: attribute_ruler, tok2vec, merge_noun_chunks, merge_entities, merge_subtokens, token_splitter, parser, beam_parser, entity_linker, ner, beam_ner, entity_ruler, lemmatizer, tagger, morphologizer, senter, sentencizer, textcat, spancat, textcat_multilabel, en.lemmatizer

In [65]:
doc = nlp("I am Mark E Tucker and I work in Investment Risk Management LLC as a Vice President")
for token in doc:
    print(token.text, token.lemma_, token.pos_, token.tag_, token.dep_,
            token.shape_, token.is_alpha, token.is_stop)

I I PRON PRP nsubj X True True
am be AUX VBP ROOT xx True True
Mark Mark PROPN NNP compound Xxxx True False
E E PROPN NNP compound X True False
Tucker Tucker PROPN NNP attr Xxxxx True False
and and CCONJ CC cc xxx True True
I I PRON PRP nsubj X True True
work work VERB VBP conj xxxx True False
in in ADP IN prep xx True True
Investment Investment PROPN NNP compound Xxxxx True False
Risk Risk PROPN NNP compound Xxxx True False
Management Management PROPN NNP compound Xxxxx True False
LLC LLC PROPN NNP pobj XXX True False
as as ADP IN prep xx True True
a a DET DT det x True True
Vice Vice PROPN NNP compound Xxxx True False
President President PROPN NNP pobj Xxxxx True False


In [64]:
from spacy import displacy
displacy.serve(doc, style="dep")

C:\Users\fmchan\AppData\Local\Programs\Python\Python39\lib\site-packages\spacy\displacy\__init__.py:97: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)



Using the 'dep' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [98]:
LABEL = "POSITION"

countEn = 0
countText = 0
training_set = []
for p in data:
    if p["language"] == "en":
        countEn = countEn + 1
        text_list = []
        for t in p["text"]:
            if len(t["text"]):
                text_list.append(t["text"])
        for r in p["relation"]:
            #print(pp["text"])
            countText = countText + 1
            if len(r["position"]):
                print(r["position"])
                for t in text_list:
                    start = t.find(r["position"])
                    if start >= 0:
                        training_item = tuple((t,{"entities":[tuple((start,start+len(r["position"]),LABEL))]}))
                        print(training_item)
                        training_set.append(training_item)
            '''
            ner_str = json.loads(pp["ner"])
            entities_list = []
            for ner in ner_str:
                #ner = json.loads(ner_str)
                #print(ner)
                if len(ner):
                    #print(ner["text"])
                    entities_list.append(tuple((ner["start"],ner["end"],ner["label"])))
            #print(entities_list)
            #if (len(entities_list)):
            training_set.append(tuple((pp["text"],{"entities":entities_list})))
            '''
print(countEn)
print(countText)
print(len(training_set))
# Closing file
f.close()

Group Chairman
('Mark E Tucker (63) Group Chairman Appointed to the Board: September 2017 Group Chairman since: October 2017', {'entities': [(19, 33, 'POSITION')]})
Group Managing Director
('Career: Noel was formally named Group Chief Executive in March 2020, having held the role on an interim basis since August 2019. He has held various management roles across HSBC since joining in 1992. He was most recently Chief Executive Ofcer of Global Commercial Banking, having been appointed to the role in December 2015 and as a Group Managing Director in September 2016. Noel joined Forward Trust Group, a subsidiary of Midland Bank, in 1987 and joined HSBC in 1992 when the Group acquired Midland Bank.', {'entities': [(334, 357, 'POSITION')]})
Group Chief Financial Ofcer
('Ewen Stevenson (54) Group Chief Financial Ofcer Appointed to the Board: January 2019', {'entities': [(20, 47, 'POSITION')]})
Independent non-executive Director
('Independent non-executive Directors', {'entities': [(0, 34, 'POSI

In [100]:
training_set = [
    ('Mark E Tucker (63) Group Chairman Appointed to the Board: September 2017 Group Chairman since: October 2017', {'entities': [(19, 33, 'POSITION')]}),
    ('Career: Noel was formally named Group Chief Executive in March 2020, having held the role on an interim basis since August 2019. He has held various management roles across HSBC since joining in 1992. He was most recently Chief Executive Ofcer of Global Commercial Banking, having been appointed to the role in December 2015 and as a Group Managing Director in September 2016. Noel joined Forward Trust Group, a subsidiary of Midland Bank, in 1987 and joined HSBC in 1992 when the Group acquired Midland Bank.', {'entities': [(334, 357, 'POSITION')]}),
    ('Ewen Stevenson (54) Group Chief Financial Ofcer Appointed to the Board: January 2019', {'entities': [(20, 47, 'POSITION')]}),
    ('Independent non-executive Directors', {'entities': [(0, 34, 'POSITION')]}),
    ('Henri de Castries (66) Independent non-executive Director Appointed to the Board: March 2016', {'entities': [(23, 57, 'POSITION')]}),
    ('External appointments: – Special Adviser to General Atlantic – Chairman of Institut Montaigne – Vice Chairman of Nestlé S.A. – Non-executive Director of the French National Foundation for Political Science – Member of the Global Advisory Council at LeapFrog Investments – Senior Independent non-executive Director of Stellantis NV', {'entities': [(279, 313, 'POSITION')]}),
    ('Laura Cha, GBM (71) Independent non-executive Director Appointed to the Board: March 2011', {'entities': [(20, 54, 'POSITION')]}),
    ('James Forese (58) Independent non-executive Director Appointed to the Board: May 2020', {'entities': [(18, 52, 'POSITION')]}),
    ('Steven Guggenheimer (55) Independent non-executive Director Appointed to the Board: May 2020', {'entities': [(25, 59, 'POSITION')]}),
    ('Independent non-executive Directors', {'entities': [(0, 34, 'POSITION')]}),
    ('Eileen Murray (62) Independent non-executive Director Appointed to the Board: July 2020', {'entities': [(19, 53, 'POSITION')]}),
    ('Heidi Miller (67) Independent non-executive Director Appointed to the Board: September 2014', {'entities': [(18, 52, 'POSITION')]}),
    ('Irene Lee (67) Independent non-executive Director Appointed to the Board: July 2015', {'entities': [(15, 49, 'POSITION')]}),
    ('Dr José Antonio Meade Kuribreña (51) Independent non-executive Director Appointed to the Board: March 2019', {'entities': [(37, 71, 'POSITION')]}),
    ('Pauline van der Meer Mohr (61) Independent non-executive Director Appointed to the Board: September 2015 Skills and experience: Pauline has extensive legal, corporate governance and human resources experience across a number of diferent sectors.', {'entities': [(31, 65, 'POSITION')]}),
    ('Jackson Tai (70) Independent non-executive Director Appointed to the Board: September 2016 Skills and experience: Jackson has signiﬁcant experience as a non-executive Director, having held senior operating and governance roles across Asia, North America and Europe.', {'entities': [(17, 51, 'POSITION')]}),
    ('David Nish (60) Independent non-executive Director Appointed to the Board: May 2016 Senior Independent non-executive Director since February 2020', {'entities': [(16, 50, 'POSITION')]}),
]

In [102]:
# Add the new label to ner
ner.add_label(LABEL)

# Resume training
optimizer = nlp.resume_training()
move_names = list(ner.move_names)

# List of pipes you want to train
pipe_exceptions = ["ner", "trf_wordpiecer", "trf_tok2vec"]

# List of pipes which should remain unaffected in training
other_pipes = [pipe for pipe in nlp.pipe_names if pipe not in pipe_exceptions]

In [103]:
with nlp.disable_pipes(*other_pipes) :

  sizes = compounding(1.0, 4.0, 1.001)
  # Training for 30 iterations     
  for itn in range(30):
    # shuffle examples before training
    random.shuffle(training_set)
    # batch up the examples using spaCy's minibatch
    batches = minibatch(training_set, size=sizes)
    # ictionary to store losses
    losses = {}
    for batch in batches:
        for text, annotations in batch:
            # create Example
            doc = nlp.make_doc(text)
            example = Example.from_dict(doc, annotations)
            # Update the model
            nlp.update([example], losses=losses, drop=0.5)
            print("Losses", losses)

Losses {'ner': 0.9479282629474716}
Losses {'ner': 0.9548484869471794}
Losses {'ner': 0.9548484869471794}
Losses {'ner': 0.9903449666652817}
Losses {'ner': 0.9903449726572275}
Losses {'ner': 0.9903699994232491}


C:\Users\fmchan\AppData\Local\Programs\Python\Python39\lib\site-packages\spacy\training\iob_utils.py:141: UserWarning: [W030] Some entities could not be aligned in the text "Independent non-executive Directors" with entities "[(0, 34, 'POSITION')]". Use `spacy.training.offsets_to_biluo_tags(nlp.make_doc(text), entities)` to check the alignment. Misaligned entities ('-') will be ignored during training.
  warnings.warn(


Losses {'ner': 0.9904271863527111}
Losses {'ner': 0.9904272758852584}
Losses {'ner': 1.0047177875218374}
Losses {'ner': 1.0047177875218374}
Losses {'ner': 1.6758139462081254}
Losses {'ner': 3.6590229017077283}
Losses {'ner': 3.65902429013144}
Losses {'ner': 3.6590249033018045}
Losses {'ner': 3.6590285975661105}
Losses {'ner': 3.6590286026994314}
Losses {'ner': 3.659028938596126}
Losses {'ner': 0.01117060472672994}
Losses {'ner': 0.011170643420458003}
Losses {'ner': 0.03188572234896736}
Losses {'ner': 0.0318896517861752}
Losses {'ner': 0.031889657209691176}
Losses {'ner': 0.032478549065623426}
Losses {'ner': 0.03247865580130669}
Losses {'ner': 0.036405144754806266}
Losses {'ner': 0.036405144754806266}
Losses {'ner': 0.036405144754806266}
Losses {'ner': 0.8058008554055632}
Losses {'ner': 0.8058008572664023}
Losses {'ner': 0.8058008598457388}
Losses {'ner': 0.8058039020783034}
Losses {'ner': 1.3998318147171196}
Losses {'ner': 1.3998318818457158}
Losses {'ner': 1.3998327044146108}
Losses {

In [109]:
# Testing the model
doc = nlp("I am Mark E Tucker and I work in Investment Risk Management LLC as a Vice President. Mark E Tucker (63) V.P. Appointed to the Board")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])

Entities []


In [122]:
countEn = 0
countText = 0
training_set = []
for p in data:
    if p["language"] == "zh":
        countEn = countEn + 1
        text_list = []
        for pp in p["text"]:
            #print(pp["text"])
            countText = countText + 1
            if len(pp["text"]):
                text_list.append(pp["text"])
            #print(pp["ner"])
            ner_str = json.loads(pp["ner"])
            entities_list = []
            for ner in ner_str:
                #ner = json.loads(ner_str)
                #print(ner)
                if len(ner):
                    #print(ner["text"])
                    entities_list.append(tuple((ner["start"],ner["end"],ner["label"])))
            #print(entities_list)
            if len(entities_list):
                training_set.append(tuple((pp["text"],{"entities":entities_list})))
print(countEn)
print(countText)
print(len(training_set))

23
2200
1666


In [129]:
import spacy # tested with v2.2.3
from spacy.pipeline import EntityRecognizer

text ="Jane lives in Boston. Jan lives in Bremen."

# load the English and German models
nlp_en = spacy.load('en_core_web_sm')  # NER tags PERSON, GPE, ...
nlp_de = spacy.load('zh_core_web_sm') # NER tags PER, LOC, ...

# the Vocab objects are not the same
assert nlp_en.vocab != nlp_de.vocab

# but the vectors are identical (because neither model has vectors)
assert nlp_en.vocab.vectors.to_bytes() == nlp_de.vocab.vectors.to_bytes()

# original English output
doc1 = nlp_en(text)
print([(ent.text, ent.label_) for ent in doc1.ents])
# [('Jane', 'PERSON'), ('Boston', 'GPE'), ('Bremen', 'GPE')]

# original German output (the German model makes weird predictions for English text)
doc2 = nlp_de(text)
print([(ent.text, ent.label_) for ent in doc2.ents])
# [('Jane lives', 'PER'), ('Boston', 'LOC'), ('Jan lives', 'PER'), ('Bremen', 'LOC')]

# initialize a new NER component with the vocab from the English pipeline
ner_de = EntityRecognizer(nlp_en.vocab)

# reload the NER component from the German model by serializing
# without the vocab and deserializing using the new NER component
ner_de.from_bytes(nlp_de.get_pipe("ner").to_bytes(exclude=["vocab"]))

# add the German NER component to the end of the English pipeline
nlp_en.add_pipe(ner_de, name="ner_de")

# check that they have the same vocab
assert nlp_en.vocab == ner_de.vocab

# combined output (English NER runs first, German second)
doc3 = nlp_en(text)
print([(ent.text, ent.label_) for ent in doc3.ents])
# [('Jane', 'PERSON'), ('Boston', 'GPE'), ('Jan lives', 'PER'), ('Bremen', 'GPE')]

[('Jane', 'PERSON'), ('Boston', 'GPE'), ('Bremen', 'GPE')]
[('Jane', 'PERSON')]


TypeError: __init__() takes at least 2 positional arguments (1 given)

In [ ]:
ner_zh=nlp_zh.get_pipe('ner')

for _, annotations in training_set:
  for ent in annotations.get("entities"):
    ner_zh.add_label(ent[2])

# Add the new label to ner
ner_zh.add_label(LABEL)

In [143]:

# Save the  model to directory
output_dir = Path('output/')
# Load the saved model and predict
print("Loading from", output_dir)
nlp = spacy.load("en_core_web_sm", exclude=["ner"])
# source NER from the same pipeline package as the last component
nlp.add_pipe("ner", source=spacy.load(output_dir))
nlp.add_pipe("entity_ruler", before="ner")
doc = nlp("I am a Executive Director and Vice President. He is a Executive Director. I am Mark E Tucker and I work in Investment Risk Management LLC as a Vice President")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])



Loading from output
Entities [('Executive Director and Vice President', 'POSITION'), ('Executive Director.', 'POSITION'), ('Investment Risk Management LLC', 'ORG')]


C:\Users\fmchan\AppData\Local\Programs\Python\Python39\lib\site-packages\spacy\pipeline\entityruler.py:335: UserWarning: [W036] The component 'entity_ruler' does not have any patterns defined.
  warnings.warn(Warnings.W036.format(name=self.name))
